In [26]:
from sklearn.preprocessing import LabelEncoder
import transformers
import torch
import nltk
import numpy as np
import pandas as pd

In [27]:
from datasets import load_dataset
dataset_train_test = load_dataset('csv', 
                                  data_files={'train': 'train_data.csv', 'test': 'test_data.csv', 'val': 'val_data.csv'})

Using custom data configuration default-b7be9a9d71194d1a


Extracting data files:   0%|          | 0/3 [00:00<?, ?it/s]

Dataset csv downloaded and prepared to /Users/fixed/.cache/huggingface/datasets/csv/default-b7be9a9d71194d1a/0.0.0/433e0ccc46f9880962cc2b12065189766fbb2bee57a221866138fb9203c83519. Subsequent calls will reuse this data.


  0%|          | 0/3 [00:00<?, ?it/s]

In [28]:
dataset_train_test

DatasetDict({
    train: Dataset({
        features: ['text', 'label'],
        num_rows: 44928
    })
    test: Dataset({
        features: ['text', 'label'],
        num_rows: 11981
    })
    val: Dataset({
        features: ['text', 'label'],
        num_rows: 14976
    })
})

In [29]:
from transformers import AutoTokenizer

tokenizer = AutoTokenizer.from_pretrained("distilbert-base-uncased")

def tokenize_function(examples):
    return tokenizer(examples["text"], padding="max_length", truncation=True)


tokenized_datasets = dataset_train_test.map(tokenize_function, batched=True)

  0%|          | 0/45 [00:00<?, ?ba/s]

  0%|          | 0/12 [00:00<?, ?ba/s]

  0%|          | 0/15 [00:00<?, ?ba/s]

In [37]:
tokenized_datasets['test'][6]

{'text': 'strategic behaviour and indicative price diffusion in paris stock   exchange auctions.   we report statistical regularities of the opening and closing auctions of french equities, focusing on the diffusive properties of the indicative auction price. two mechanisms are at play as the auction end time nears: the typical price change magnitude decreases, favoring underdiffusion, while the rate of these events increases, potentially leading to overdiffusion. a third mechanism, caused by the strategic behavior of traders, is needed to produce nearly diffusive prices: waiting to submit buy orders until sell orders have decreased the indicative price and vice-versa. ',
 'label': 6,
 'input_ids': [101,
  6143,
  9164,
  1998,
  24668,
  3976,
  19241,
  1999,
  3000,
  4518,
  3863,
  10470,
  2015,
  1012,
  2057,
  3189,
  7778,
  3180,
  6447,
  1997,
  1996,
  3098,
  1998,
  5494,
  10470,
  2015,
  1997,
  2413,
  1041,
  15549,
  7368,
  1010,
  7995,
  2006,
  1996,
  4487,
 

In [31]:
def torch_dataset(dataset):
    dataset = dataset.remove_columns(["text"])
    dataset = dataset.rename_column("label", "labels")
    dataset.set_format("torch")
    return dataset

train_dataset = torch_dataset(tokenized_datasets['train'])
val_dataset = torch_dataset(tokenized_datasets['val'])
test_dataset = torch_dataset(tokenized_datasets['test'])

In [32]:
train_dataset.to_json("train_dataset.json")
val_dataset.to_json("val_dataset.json")
test_dataset.to_json("test_dataset.json")

Creating json from Arrow format:   0%|          | 0/5 [00:00<?, ?ba/s]

Creating json from Arrow format:   0%|          | 0/2 [00:00<?, ?ba/s]

Creating json from Arrow format:   0%|          | 0/2 [00:00<?, ?ba/s]

32655572